<span style='color:gray'> <span style="font-size:25px;"> **Development of "Machine Learning Models"  (Workflow)**
    
In this Notebook, the machine learning model will be created and then the data from well-logs DLIS file [after preprocessing, sorting and finalizing the data] is loaded as input for Machine Learning model (ML); 
* Random Forest Regressor
* Gradient Boosting Regressor
    
    
For the prediction of petrophysical properties, such as porosity, permeability and water saturation, these two Regressor models **Random Forest Regressor** and **Gradient Boosting Regressor** are suitable.

They are Ensemble Based Tree Methods; they are based on the generation of Decision Trees.

We use Regression Models since we want to predict a continuous variable.

**Advantages** of the 2 regression models, since they are based on Decision Trees:

* They do not need the normalization or scaling of the original dataset;
* They are not sensitive to outliers, thus, outliers detection and removal are not required.

**==================================================================================================================**
    
In well-log machine learning models, the choice between regression and classification (Supervised ML) depends on the nature of the problem you are trying to solve and the type of data you have. Let's break down the reasons why regression is often preferred over classification in this context:

**Continuous Output**: Well-log data often involves continuous measurements such as porosity, permeability, resistivity, and other geological properties. Regression is well-suited for predicting and modeling continuous numerical values. Classification, on the other hand, is typically used when the output is categorical or discrete, like classifying lithology or rock types.

**Data Distribution**: Well-log data tends to have a wide range of continuous values. Using classification would require discretizing this data into bins or classes, which can lead to loss of information and potentially introduce biases. Regression models can capture the nuances and variations present in the continuous data more effectively.

**Evaluation Metrics**: Regression models are evaluated using metrics such as mean squared error (MSE), root mean squared error (RMSE), or mean absolute error (MAE). These metrics are well-suited for measuring the accuracy of predictions involving continuous values. Classification models, on the other hand, use metrics like accuracy, precision, recall, and F1-score, which are designed for categorical predictions.

**Feature Importance**: Well-log data analysis often involves understanding the relationships between different geological features and the target property. Regression models can provide insights into the quantitative impact of each feature on the predicted values, aiding in geological interpretation.


<span style='color:gray'> <span style="font-size:20px;"> 
**Importing Libraries, Regressors, and Required Dependencies**

In [9]:
%pip install --quiet --upgrade scikit-learn==1.2.2
%pip install --quiet qbstyles


# Importing the dependencies
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt
import seaborn as sns

from qbstyles import mpl_style
mpl_style(dark=False)  # Set light matplotlib style

import matplotlib.patches as mpatches  # To create a legend with a color box
import pickle

# Importing the models 
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.multioutput import MultiOutputRegressor

from sklearn.linear_model import LinearRegression, Ridge, Lasso, ElasticNet
from sklearn.tree import DecisionTreeRegressor
from sklearn.svm import SVR
from sklearn.neighbors import KNeighborsRegressor
from sklearn.preprocessing import PolynomialFeatures
from sklearn.neural_network import MLPRegressor
                                         
from sklearn.model_selection import RandomizedSearchCV

# train_test_split is a function 
# cross_val_score and KFold are functions

from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score, KFold 

# Regression metrics
from sklearn.metrics import r2_score, mean_squared_error, mean_squared_error, mean_absolute_error

# The package "Matplotlib Inline Back-end" provides support for Matplotlib to display figures directly inline
# "svg" stands for "scalable vector graphic". The plot can be scaled without compromising its quality
from matplotlib_inline.backend_inline import set_matplotlib_formats
set_matplotlib_formats('svg')

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


# ========================================================

<span style='color:gray'> <span style="font-size:20px;">**Load the Random Forest & Gradient Boosting Models**</span> </span>

In [10]:
# Define the full path to the save file
save_path = '/Users/amirhosseinakhondzadeh/CODE_WELLLOGS/Petrobras Well-log Analysis/Processed Data (out put of preprocessing == Input of ML)/Output of Predictive Models/random_forest.pickle'

with open(save_path, "rb") as file:      # Unpickle the Random Forest model
    RandomForest_model = pickle.load(file)

In [11]:
# Define the full path to the save file
save_path = '/Users/amirhosseinakhondzadeh/CODE_WELLLOGS/Petrobras Well-log Analysis/Processed Data (out put of preprocessing == Input of ML)/Output of Predictive Models/gradient_boosting.pickle'

with open(save_path, "rb") as file:      # Unpickle the Random Forest model
    GradientBoosting_model = pickle.load(file)

<span style='color:gray'> <span style="font-size:15px;"> **Loading entire dataset on the model**</span> </span>

You can use the loaded model to compute predictions

We perform the prediction on the entire original dataset 

New prediction on the entire dataset

RandomForest_model
GradientBoosting_model


y_test_EFF, y_pred_rf_EFF

y_test_FF, y_pred_rf_FF

y_test_TOT, y_pred_rf_TOT

=====

y_test_EFF, y_pred_gb_EFF

y_test_FF, y_pred_gb_FF

y_test_TOT, y_pred_gb_TOT

==================



In [14]:
file_path = '/Users/amirhosseinakhondzadeh/CODE_WELLLOGS/Petrobras Well-log Analysis/Processed Data (out put of preprocessing == Input of ML)/Output of well data, [unique dataframe creation]/df_Fin.csv'
df = pd.read_csv(file_path)

In [15]:
predictors = ["GR", "AT90", "RHOZ", "NPHI", "DTCO", "PEFZ"]  
outputs = ["NMREFF","NMRFF","NMRTOT"]  # They are predicted at the same time 

X = df[predictors]
y = df[outputs]

In [36]:
y_prediction_rf = RandomForest_model.predict(X)

# Extract the predicted values for output 1, output 2 and output 3
y_prediction_rf_EFF = y_prediction_rf[:, 0]
y_prediction_rf_FF = y_prediction_rf[:, 1]
y_prediction_rf_TOT = y_prediction_rf[:, 2]


# Measurement Values of Y (NMR ==> EFECTIVE, Free Fluid, TCMR)
y_EFF = y.drop(columns=["NMRFF","NMRTOT"])      # CMRP_3MS [EFECTIVE Porosity]
y_FF = y.drop(columns=["NMREFF","NMRTOT"])   # CMFF [Free Fluid Porosity]
y_TOT = y.drop(columns=["NMREFF","NMRFF"])  # TCMR [Total Porosity]

array([21.97079952, 24.80015715, 25.88214502, ...,  0.06765381,
        0.06765381,  0.06765381])

In [51]:
# Permeability
FF = y_prediction_rf_FF
PHI_tot = y_prediction_rf_TOT
BF = y_prediction_rf_TOT - y_prediction_rf_FF
a = 10**4
b = 2
c = 4

# Calculate k
k = a * ((FF / BF) ** b) * ((PHI_tot / 10) ** c)

#================================================
# Saturation
FF = y_prediction_rf_FF
PHI_eff = y_prediction_rf_EFF

Swie = (PHI_eff-FF)/ PHI_eff

<span style='color:gray'> <span style="font-size:30px;">**Plots**</span> </span>

<span style='color:gray'> <span style="font-size:20px;">**Random Forest - Scatter Plot**</span> </span>

In [38]:
# Random Forest Scatter Plots 
fig, ax = plt.subplots(3,1, figsize=(10,25))
fig.suptitle("RANDOM FOREST SCATTER PLOTS", fontsize=25, fontweight='bold')
fig.subplots_adjust(top=0.89,hspace=0.4)

#Set up the subplots grid
ax1 = plt.subplot2grid((3,1),(0,0),rowspan=1,colspan=1) 
ax2 = plt.subplot2grid((3,1),(1,0),rowspan=1,colspan=1) 
ax3 = plt.subplot2grid((3,1),(2,0),rowspan=1,colspan=1) 


# First Scatter Plot
ax1.scatter(y_EFF,y_prediction_rf_EFF, s=80, c='lime', edgecolors='magenta')
ax1.set_xlabel('Well-log measurement', fontsize=12) 
ax1.set_ylabel('Well-log prediction', fontsize=12)
ax1.set_title('Total Dataset - NMR Effective Porosity (m3/m3)', fontsize=16, fontweight='bold')
ax1.set_xlim(0,0.25)
ax1.set_ylim(0,0.25)
ax1.set_xticks(np.arange(0, 0.25, 0.025))
ax1.set_yticks(np.arange(0, 0.25, 0.025))

# Second Scatter Plot
ax2.scatter(y_FF,y_prediction_rf_FF, s=80, c='blue', edgecolors='magenta')
ax2.set_xlabel('Well-log measurement', fontsize=12) 
ax2.set_ylabel('Well-log prediction', fontsize=12)
ax2.set_title('Total Dataset - NMR Free Fluid (m3/m3)', fontsize=16, fontweight='bold')
ax2.set_xlim(0,0.200)
ax2.set_ylim(0,0.200)
ax2.set_xticks(np.arange(0, 0.200, 0.025))
ax2.set_yticks(np.arange(0, 0.200, 0.025))

# Third Scatter Plot 
ax3.scatter(y_TOT,y_prediction_rf_TOT, s=80, c='gold', edgecolors='magenta')
ax3.set_xlabel('Well-log measurement', fontsize=12) 
ax3.set_ylabel('Well-log prediction', fontsize=12)
ax3.set_title('Total Dataset - NMR Total Porosity (m3/m3)', fontsize=16, fontweight='bold')
ax3.set_xlim(0,0.200)
ax3.set_ylim(0,0.200)
ax3.set_xticks(np.arange(0, 0.200, 0.025))
ax3.set_yticks(np.arange(0, 0.200, 0.025))


# Add a black border to each subplot
for ax in [ax1,ax2,ax3]:
    ax.spines['top'].set_color('black')
    ax.spines['bottom'].set_color('black')
    ax.spines['left'].set_color('black')
    ax.spines['right'].set_color('black')
    
# Set font size of the tick labels
for ax in [ax1,ax2,ax3]:
    ax.tick_params(axis='x', labelsize=12)
    ax.tick_params(axis='y', labelsize=12)
    
# Set grid 
for ax in [ax1,ax2,ax3]:
    ax.grid(color='black',lw=0.5)

<span style='color:gray'> <span style="font-size:20px;">**Random Forest - Well-log Plot**</span> </span>

In [39]:
# Otput 1, Output 2 and Output 3 should be converted into arrays 
y_EFF = np.array(y_EFF)
y_FF = np.array(y_FF)
y_TOT = np.array(y_TOT)

In [67]:
# Another way to perform comparison between the well log measurements and the predicted values 
fig, axes = plt.subplots(nrows=1, ncols=6, figsize=(12,20))
fig.suptitle("RANDOM FOREST PLOTS", fontsize=25, fontweight='bold')
fig.subplots_adjust(top=0.8, wspace=0.15)

track_names = ['EFFNMR (m3/m3)','FFNMR(m3/m3)','TOTNMR(m3/m3)','CMRP_3MS(m3/m3)','CMFF(m3/m3)','TCMR(m3/m3)']


#Set up the subplots grid
ax1 = plt.subplot2grid((1,6),(0,0),rowspan=1,colspan=1) 
ax2 = plt.subplot2grid((1,6),(0,1),rowspan=1,colspan=1) 
ax3 = plt.subplot2grid((1,6),(0,2),rowspan=1,colspan=1) 
ax4 = plt.subplot2grid((1,6),(0,3),rowspan=1,colspan=1) 
ax5 = ax4.twiny()
ax6 = ax4.twiny()
ax7 = plt.subplot2grid((1,6),(0,4),rowspan=1,colspan=1) 
ax8 = plt.subplot2grid((1,6),(0,5),rowspan=1,colspan=1) 

x_ax = range(len(X))

#==================
# First Plot
ax1.plot(y_EFF, x_ax, color = "olive", lw = 0.5, linestyle = '--')
ax1.plot(y_prediction_rf_EFF, x_ax, color = "lime", lw = 0.25, linestyle = '-')  
ax1.set_xlabel('CMRP_3MS(m3/m3)',fontsize=14, color='black') 
ax1.set_ylabel('Total Dataset Index',fontsize=14)
legend1 = ax1.legend(["Measured NMR Effective Porosity", "Predicted NMR Effective Porosity"], loc= 'lower center',fontsize='small', framealpha=0.7)

#==================
# Second Plot
ax2.plot(y_FF, x_ax, color = "aqua", lw = 0.5, linestyle = '--')
ax2.plot(y_prediction_rf_FF, x_ax, color = "blue", lw = 0.25, linestyle = '-')
ax2.set_xlabel('CMFF(m3/m3)',fontsize=14, color='black')
legend2 = ax2.legend(["Measured NMR Free Fluid", "Predicted NMR Free Fluid"], loc= 'lower center',fontsize='small', framealpha=0.7)

#==================
# Third Plot 
ax3.plot(y_TOT, x_ax, color = "darkred", lw = 0.5, linestyle = '--')
ax3.plot(y_prediction_rf_TOT, x_ax, color = "gold", lw = 0.25, linestyle = '-')
ax3.set_xlabel('TCMR(m3/m3)',fontsize=14, color='black')
legend3 = ax3.legend(["Measured NMR Total Porosity", "Predicted NMR Total Porosity"], loc= 'lower center',fontsize='small', framealpha=0.7)

#==================
# Fourth Plot
ax4.plot(y_prediction_rf_EFF, x_ax, color = "lime", lw = 1, linestyle = '-')                                                    
ax4.spines['top'].set_position(('outward',100))
ax4.set_xlabel('CMRP_3MS(m3/m3)',fontsize=14, color='lime') 
ax4.tick_params(axis='x', colors='lime', labelsize=12)
ax4.spines["top"].set_edgecolor("lime")

ax5.plot(y_prediction_rf_FF, x_ax, color = "blue", lw = 1, linestyle = '-' )
ax5.spines['top'].set_position(('outward',50))
ax5.set_xlabel('CMFF(m3/m3)', fontsize=14, color='blue') 
ax5.tick_params(axis='x', colors='blue', labelsize=12)
ax5.spines["top"].set_edgecolor("blue")

ax6.plot(y_prediction_rf_TOT, x_ax, color = "gold", lw = 1, linestyle = '-' )                                                  
ax6.spines['top'].set_position(('outward',0))
ax6.set_xlabel('TCMR(m3/m3)', fontsize=14, color='gold')
ax6.tick_params(axis='x', colors='gold', labelsize=12)
ax6.spines["top"].set_edgecolor("gold")

# Add shading in Fifth Track with fill_betweenx(y, left handside value, x)
ax4.fill_betweenx(x_ax,y_prediction_rf_FF,0,                   facecolor='blue', alpha=0.5, interpolate=True)
ax4.fill_betweenx(x_ax,y_prediction_rf_EFF,y_prediction_rf_FF, facecolor='lime', alpha=0.5, interpolate=True)
ax4.fill_betweenx(x_ax,y_prediction_rf_TOT,y_prediction_rf_EFF, facecolor='gold', alpha=0.5, interpolate=True)

# Create legend for Fifth Track 
Clay_Bound_Water = mpatches.Patch(color='gold', label='CLAY BOUND WATER')
Bound_Water      = mpatches.Patch(color='lime', label='BOUND WATER')
Free_Fluid       = mpatches.Patch(color='blue', label='FREE FLUID')
legend4 = ax4.legend(handles=[Clay_Bound_Water, Bound_Water, Free_Fluid], loc='upper left', fontsize='small', framealpha=0.7)

#==================

#ax7.plot(k, x_ax, color = "darkred", lw = 0.5, linestyle = '--')
#ax7.plot(k, x_ax, color="darkred", lw=0.5, linestyle='--', marker='o', markersize=2)
#ax7.plot(k, x_ax, color="darkred", lw=0.5, linestyle='--', marker='o', markersize=2, alpha=0.5)

# Choose the degree of the polynomial curve
n = 40  # Choose the subsampling factor (e.g., every 10th data point)

"""
degree = 3  # You can adjust this degree as needed

# Fit a polynomial curve to the subsampled data
coefficients = np.polyfit(k[::n], x_ax[::n], degree)

# Create a range of x values for the curve
x_range = np.linspace(min(k[::n]), max(k[::n]), 100)

# Calculate the corresponding y values for the curve
y_curve = np.polyval(coefficients, x_range)
"""


n = 40  # Choose the subsampling factor (e.g., every 10th data point)
ax7.plot(k[::n], x_ax[::n], color="darkred", lw=0.5, linestyle='--', marker='o', markersize=2)
#ax7.plot(x_range, y_curve, color="blue", lw=2, linestyle='-')  # Add the polynomial curve

ax7.set_xlim(0.00001,10000000) 
ax7.semilogx()                                                            
ax7.set_xlabel('Permeability(mD)',fontsize=14, color='black')
legend5 = ax7.legend(["Predicted NMR Permeability (mD)"], loc= 'lower center',fontsize='small', framealpha=0.7)

#==================
#ax8.plot(Swie*100, x_ax, color = "darkred", lw = 0.5, linestyle = '--')

n = 40  # Choose the subsampling factor (e.g., every 10th data point)
ax8.plot(k[::n], x_ax[::n], color="darkred", lw=0.5, linestyle='--', marker='o', markersize=2)

ax8.set_xlim(0.0001,50) 
ax8.semilogx()                                                            
ax8.set_xlabel('Saturation (%)',fontsize=14, color='black')
legend6 = ax8.legend(["Predicted Effective saturation (%)"], loc= 'lower center',fontsize='small', framealpha=0.7)




# Set xlim() and ylim()
for ax in [ax1,ax2,ax3,ax4,ax5,ax6]:
    ax.set_xlim(20,0.001)
    ax.set_ylim(11000,0) 



# Add a black border to each subplot
for ax in [ax1,ax2,ax3,ax4,ax5,ax6]:
    ax.spines['top'].set_color('black')
    ax.spines['bottom'].set_color('black')
    ax.spines['left'].set_color('black')
    ax.spines['right'].set_color('black')
    
# Set font size of the tick labels
for ax in [ax1,ax2,ax3,ax4,ax5,ax6]:
    ax.tick_params(axis='x', labelsize=12)
    ax.tick_params(axis='y', labelsize=12)
    
# Set grid 
for ax in [ax1,ax2,ax3,ax4,ax5,ax6]:
    ax.grid(color='black',lw=0.7)
    
# Hide tick labels on the y-axis
for ax in [ax2,ax3,ax4,ax5,ax6, ax7, ax8]:
    plt.setp(ax.get_yticklabels(), visible=False)
    
# Set border properties of the legend 
for legend in [legend1,legend2,legend3,legend4]:
    legend.get_frame().set_linewidth(2)
    legend.get_frame().set_edgecolor('black')
    
# Set xlabel and xticks position 
for ax in [ax1,ax2,ax3,ax4,ax5,ax6, ax7, ax8]:
    ax.xaxis.set_label_position("top")
    ax.xaxis.set_ticks_position("top")

In [ ]:
y_prediction_gb = GradientBoosting_model.predict(X)

# Extract the predicted values for output 1, output 2 and output 3
y_prediction_gb_EFF = y_prediction_gb[:, 0]
y_prediction_gb_FF = y_prediction_gb[:, 1]
y_prediction_gb_TOT = y_prediction_gb[:, 2]

In [ ]:
#=====
Permeability Calculation